# Cancelled cases prediction model

Predictive model to identify patients at high risk of canceling or not showing up for their scheduled surgeries. By analyzing historical data, such as patient demographics, case type, cases history, the model can generate risk scores. The idea is to send nudges to schedulers to be able to take actions based on the results.


## Impact

This project is cool and impactful because it addresses a major inefficiency in perioperative workflows—unanticipated schedule gaps due to cancellations or no-shows. By proactively mitigating these gaps, hospitals can:
- Increase OR utilization rates.
- Enhance patient satisfaction by rescheduling possible canceled cases more efficiently.
- Reduce revenue loss associated with unused OR time.
- Enable perioperative teams to focus on patient care rather than scrambling to adjust schedules last minute.


## Development

First, setting up the environment for use.

In [218]:
import pandas as pd
import numpy
import statsmodels.api as sm
import seaborn as sns
import matplotlib.pyplot as plt
from ydata_profiling import ProfileReport
from geopy.geocoders import Nominatim
import scipy 
from scipy import stats 
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix, roc_curve, auc, ConfusionMatrixDisplay, f1_score

from sklearn.naive_bayes import GaussianNB



Importing the dataset, in this case this data was obtained from the query **[<code>select case_cancellation_time, hospital, scheduled_surgery_date, patient_class, h.latitude as hospital_latitude, h.longitude as hospital_longitude, patient_age_months, patient_gender_client, patient_race_client, patient_weight_in_kg, patient_home_zip_code, patient_language_client, primary_payor_client, case_specialty, count_scheduled_procedures_in_case, scheduled_primary_procedure_id, scheduled_wheelsin_to_wheelsout_min_derived, days_scheduled_in_advance, case_status_class from public.or_cases_golden_scheduled cases
inner join analyticsmd.main_hospital h on cases.hospital = h.id
where scheduled_surgery_date >= '2024-01-01';<code>](https://github.com/analyticsMD/standard-solution-views/blob/master/models/or/base_or/all_other_base_or/or_cases_logs_golden_view.sql)** from Standard Solution Views. 

In [10]:
cases = pd.read_csv('/Users/jennysanchez/Documents/Jenny/Hackathon 2025/2025-q-hackathon/Cases.csv', low_memory=False)
print("Shape of DataFrame:", cases.shape)
print("Memory Usage (MB):", cases.memory_usage(deep=True).sum() / (1024 ** 2))

Shape of DataFrame: (194776, 18)
Memory Usage (MB): 135.0183811187744


In [11]:
cases.dtypes

CASE_CANCELLATION_TIME                          object
HOSPITAL                                         int64
SCHEDULED_SURGERY_DATE                          object
PATIENT_CLASS                                   object
PATIENT_FINANCIAL_ID                            object
PATIENT_AGE_MONTHS                             float64
PATIENT_GENDER_CLIENT                           object
PATIENT_RACE_CLIENT                             object
PATIENT_WEIGHT_IN_KG                           float64
PATIENT_HOME_ZIP_CODE                           object
PATIENT_LANGUAGE_CLIENT                         object
PRIMARY_PAYOR_CLIENT                            object
CASE_SPECIALTY                                  object
COUNT_SCHEDULED_PROCEDURES_IN_CASE             float64
SCHEDULED_PRIMARY_PROCEDURE_ID                 float64
SCHEDULED_WHEELSIN_TO_WHEELSOUT_MIN_DERIVED    float64
DAYS_SCHEDULED_IN_ADVANCE                      float64
CASE_STATUS_CLASS                               object
dtype: obj

---
## Data Cleaning

### Data profiling

Executing a data profiling report to identify main misses in variables.

In [15]:
profile = ProfileReport(cases, title = "Cases stats")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

---
0.  Dropping unneeded variables.

In [52]:
cases = cases.drop(columns=['PATIENT_FINANCIAL_ID'])


a. Dropping column SCHEDULED_PRIMARY_PROCEDURE_ID since it has positive linear correlation with CASE_SPECIALTY (>0.75).

In [54]:
cases = cases.drop(columns=['SCHEDULED_PRIMARY_PROCEDURE_ID'])


---
1.  Dropping duplicates.

In [21]:
cases.drop_duplicates(inplace=True)

In [109]:
cases['SCHEDULED_SURGERY_DATE'] = pd.to_datetime(cases['SCHEDULED_SURGERY_DATE'])

---
2. Addressing null values, choosing to assign the mode/median in the majority of variables. 

For **Case Cancellation Time**, we assign a date in the far future, because those cases are not changing their status to canceled, they were already performed or currently scheduled.

In [58]:
cases['CASE_CANCELLATION_TIME'] = pd.to_datetime(cases['CASE_CANCELLATION_TIME'])

In [60]:
cases['CASE_CANCELLATION_TIME'] = cases['CASE_CANCELLATION_TIME'].fillna(pd.Timestamp('2100-01-01 00:00:01'))


For **Patient Gender**, assigning Other 

In [62]:
cases['PATIENT_GENDER_CLIENT'] = cases['PATIENT_GENDER_CLIENT'].fillna("OTH")


For **Patient Class** , assigning the mode.

In [64]:
cases['PATIENT_CLASS'] = cases['PATIENT_CLASS'].fillna(cases['PATIENT_CLASS'].mode())


For **Patient Weight** , assigning the median.

In [66]:
cases['PATIENT_WEIGHT_IN_KG'] = cases['PATIENT_WEIGHT_IN_KG'].fillna(cases['PATIENT_WEIGHT_IN_KG'].median())


For **Patient Race** , assigning the mode.

In [68]:
cases['PATIENT_RACE_CLIENT'] = cases['PATIENT_RACE_CLIENT'].fillna(cases['PATIENT_RACE_CLIENT'].mode())


For **Patient age** , assigning the median.

In [70]:
cases['PATIENT_AGE_MONTHS'] = cases['PATIENT_AGE_MONTHS'].fillna(cases['PATIENT_AGE_MONTHS'].median())


For **Days scheduled in advance** , assigning the median.

In [72]:
cases['DAYS_SCHEDULED_IN_ADVANCE'] = cases['DAYS_SCHEDULED_IN_ADVANCE'].fillna(cases['DAYS_SCHEDULED_IN_ADVANCE'].median())


For **Scheduled wheels in to wheels out derived** , assigning the median.

In [74]:
cases['SCHEDULED_WHEELSIN_TO_WHEELSOUT_MIN_DERIVED'] = cases['SCHEDULED_WHEELSIN_TO_WHEELSOUT_MIN_DERIVED'].fillna(cases['SCHEDULED_WHEELSIN_TO_WHEELSOUT_MIN_DERIVED'].median())


For **Count of scheduled procedures in case** , assigning the median.

In [76]:
cases['COUNT_SCHEDULED_PROCEDURES_IN_CASE'] = cases['COUNT_SCHEDULED_PROCEDURES_IN_CASE'].fillna(cases['COUNT_SCHEDULED_PROCEDURES_IN_CASE'].median())


For **Patient Language** , assigning the mode.

In [82]:
cases['PATIENT_LANGUAGE_CLIENT'] = cases['PATIENT_LANGUAGE_CLIENT'].fillna(cases['PATIENT_LANGUAGE_CLIENT'].mode())


For **Primary Payor** , assigning the mode.

In [78]:
cases['PRIMARY_PAYOR_CLIENT'] = cases['PRIMARY_PAYOR_CLIENT'].fillna(cases['PRIMARY_PAYOR_CLIENT'].mode())


For **Primary Payor** , assigning the mode.

In [78]:
cases['PATIENT_HOME_ZIP_CODE'] = cases['PATIENT_HOME_ZIP_CODE'].fillna(cases['PATIENT_HOME_ZIP_CODE'].mode())


For **Case specialty** , assigning the mode.

In [87]:
cases['CASE_SPECIALTY'] = cases['CASE_SPECIALTY'].fillna(cases['CASE_SPECIALTY'].mode())


Creating dummies for categorical variables.

In [103]:
gender = pd.get_dummies(cases['PATIENT_GENDER_CLIENT'])
case_specialty = pd.get_dummies(cases['CASE_SPECIALTY'])
primary_payor_client = pd.get_dummies(cases['PRIMARY_PAYOR_CLIENT'])
patient_language_client = pd.get_dummies(cases['PATIENT_LANGUAGE_CLIENT'])
## TBD patient_home_zip_code = pd.get_dummies(cases['PATIENT_HOME_ZIP_CODE'])
patient_race_client = pd.get_dummies(cases['PATIENT_RACE_CLIENT'])
patient_class = pd.get_dummies(cases['PATIENT_CLASS'])
hospital = pd.get_dummies(cases['HOSPITAL'])


In [157]:
cases["case_target"] = cases["CASE_STATUS_CLASS"].transform(lambda x: True if x == 'CANCELED' else False)

In [159]:
cases["year"] = cases["SCHEDULED_SURGERY_DATE"].dt.year
cases["month"] = cases["SCHEDULED_SURGERY_DATE"].dt.month
cases["day"] = cases["SCHEDULED_SURGERY_DATE"].dt.day
cases["cancel_year"] = cases["CASE_CANCELLATION_TIME"].dt.year
cases["cancel_month"] = cases["CASE_CANCELLATION_TIME"].dt.month
cases["cancel_day"] = cases["CASE_CANCELLATION_TIME"].dt.day

---
3. Standardizing numerical variables.

In [162]:
cases["day"] = stats.zscore(cases['day'])
cases["month"] = stats.zscore(cases['month'])
cases["year"] = stats.zscore(cases['year'])
cases["cancel_day"] = stats.zscore(cases['cancel_day'])
cases["cancel_month"] = stats.zscore(cases['cancel_month'])
cases["cancel_year"] = stats.zscore(cases['cancel_year'])
cases['surgery_mins'] = stats.zscore(cases['SCHEDULED_WHEELSIN_TO_WHEELSOUT_MIN_DERIVED'])
cases['days_scheduled_in_advance'] = stats.zscore(cases['DAYS_SCHEDULED_IN_ADVANCE'])
cases['patient_age'] = stats.zscore(cases['PATIENT_AGE_MONTHS'])
cases['patient_weight'] = stats.zscore(cases['PATIENT_WEIGHT_IN_KG'])

In [164]:
final_cases_cat = pd.concat([gender, case_specialty, primary_payor_client, patient_language_client, patient_race_client, patient_class, hospital, cases['case_target']], axis=1 )
final_cases_num = pd.concat(
    [cases["day"],
     cases["month"],
     cases["year"],
     cases["cancel_day"],
     cases["cancel_month"],
     cases["cancel_year"],
     cases['surgery_mins'],
     cases['days_scheduled_in_advance'],
     cases['patient_age'],
     cases['patient_weight']
    ], axis=1)
final_cases = pd.concat([final_cases_num, final_cases_cat], axis=1)

In [212]:
final_cases.info()

<class 'pandas.core.frame.DataFrame'>
Index: 194722 entries, 0 to 194775
Columns: 219 entries, day to case_target
dtypes: bool(209), float64(10)
memory usage: 55.2 MB


In [166]:
na_count = final_cases.isna().sum().sum()

print(na_count)


0


---
## Models

In [184]:
y = final_cases["case_target"]
X = final_cases.drop(columns = ["case_target"])
X.columns = X.columns.astype(str)

X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42)

1. Logistic Regression

In [186]:
# Train the Logistic Regression model
model = LogisticRegression()
model.fit(X_train, y_train)

LogisticRegression()

In [188]:
# Evaluate the model
y_pred = model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy: {:.2f}%".format(accuracy * 100))

Accuracy: 99.66%


In [190]:
print("Confusion Matrix:\n", confusion_matrix(y_test, y_pred))
print("\nClassification Report:\n", classification_report(y_test, y_pred))

Confusion Matrix:
 [[32959    12]
 [  120  5854]]

Classification Report:
               precision    recall  f1-score   support

       False       1.00      1.00      1.00     32971
        True       1.00      0.98      0.99      5974

    accuracy                           1.00     38945
   macro avg       1.00      0.99      0.99     38945
weighted avg       1.00      1.00      1.00     38945



2. Naive Bayes Classifier

In [214]:
model = GaussianNB()

model.fit(X_train, y_train);

In [220]:

y_pred = model.predict(X_test)

accuray = accuracy_score(y_pred, y_test)
f1 = f1_score(y_pred, y_test, average="weighted")

print("Accuracy:", accuray)
print("F1 Score:", f1)

Accuracy: 0.41453331621517525
F1 Score: 0.3766471468144384
